In [ ]:
import folium
import pandas as pd
import branca.colormap as cm
import json
import requests
import io
from shapely.geometry import shape

# Load the CSV file
cost_df = pd.read_csv("data/CostOfLiving.csv")

# Clean column names
cost_df.columns = cost_df.columns.str.strip()

# Create base map centered on a global view
world_map = folium.Map(
    location=[20, 0],
    zoom_start=2,
    tiles="OpenStreetMap", 
    scrollWheelZoom=True,
    control_scale=True,
    width='100%',
    height='100%'
)

# Define the GeoJSON URL
geojson_url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/world-countries.json'

# Download the GeoJSON data
geo_data = requests.get(geojson_url).json()

# Define metrics with display names (in desired order)
metrics = [
    ('Cost of Living Index', 'Cost of Living Index'),
    ('Rank', 'Cost of Living Rank'),
    ('Rent Index', 'Rent Index'),
    ('Cost of Living Plus Rent Index', 'Cost of Living + Rent'),
    ('Groceries Index', 'Groceries Index'),
    ('Restaurant Price Index', 'Restaurant Prices'),
    ('Local Purchasing Power Index', 'Purchasing Power')
]

# Define a mapping dictionary for country name standardization
country_name_map = {
    'United States': 'United States of America',
    'Russia': 'Russian Federation',
    'South Korea': 'Korea, Republic of',
    'Iran': 'Iran, Islamic Republic of',
    'Vietnam': 'Viet Nam',
    'Venezuela': 'Venezuela, Bolivarian Republic of',
    'Tanzania': 'Tanzania, United Republic of',
    'Syria': 'Syrian Arab Republic',
    'Moldova': 'Moldova, Republic of',
    'Taiwan': 'Taiwan, Province of China',
    'Bolivia': 'Bolivia, Plurinational State of',
    'Ivory Coast': "Côte d'Ivoire",
    'North Macedonia': 'Macedonia, the former Yugoslav Republic of',
    'Libya': 'Libyan Arab Jamahiriya',
    'Bosnia And Herzegovina': 'Bosnia and Herzegovina',
    'Brunei': 'Brunei Darussalam',
    'United Kingdom': 'United Kingdom',
    'Us Virgin Islands': 'Virgin Islands, U.S.',
    'Hong Kong (China)': 'Hong Kong',
    'Macao (China)': 'Macao',
    'China': 'China',
    'Kosovo (Disputed Territory)': 'Kosovo',
    'Trinidad And Tobago': 'Trinidad and Tobago',
    'United Arab Emirates': 'United Arab Emirates',
    'Dominican Republic': 'Dominican Republic',
    'Czech Republic': 'Czech Republic',
    'New Zealand': 'New Zealand',
    'Costa Rica': 'Costa Rica',
    'El Salvador': 'El Salvador',
    'Saudi Arabia': 'Saudi Arabia',
    'South Africa': 'South Africa',
    'Papua New Guinea': 'Papua New Guinea',
    'Netherlands': 'Netherlands'
}

# Standardize country names in the DataFrame
for index, row in cost_df.iterrows():
    country = row['Country'].strip()
    if country in country_name_map:
        cost_df.at[index, 'Country_Mapped'] = country_name_map[country]
    else:
        cost_df.at[index, 'Country_Mapped'] = country

# Normalize all metrics to 0-100 scale
for col, _ in metrics:
    if col == 'Rank':
        # For Rank, lower is better so reverse the normalization
        max_rank = cost_df[col].max()
        cost_df[f'Normalized_{col}'] = 100 * (1 - (cost_df[col] - 1) / (max_rank - 1))
    else:
        # For other metrics, normalize to 0-100
        min_val = cost_df[col].min()
        max_val = cost_df[col].max()
        cost_df[f'Normalized_{col}'] = 100 * (cost_df[col] - min_val) / (max_val - min_val)

# Create mapping dict for tooltips with normalized data
country_data = {}
for _, row in cost_df.iterrows():
    try:
        country_data[row['Country_Mapped']] = {
            'Rank': int(row['Rank']),
            'Cost of Living Index': float(row['Cost of Living Index']),
            'Rent Index': float(row['Rent Index']),
            'Cost of Living Plus Rent Index': float(row['Cost of Living Plus Rent Index']),
            'Groceries Index': float(row['Groceries Index']),
            'Restaurant Price Index': float(row['Restaurant Price Index']),
            'Local Purchasing Power Index': float(row['Local Purchasing Power Index']),
            # Add normalized values
            'Normalized_Rank': float(row['Normalized_Rank']),
            'Normalized_Cost of Living Index': float(row['Normalized_Cost of Living Index']),
            'Normalized_Rent Index': float(row['Normalized_Rent Index']),
            'Normalized_Cost of Living Plus Rent Index': float(row['Normalized_Cost of Living Plus Rent Index']),
            'Normalized_Groceries Index': float(row['Normalized_Groceries Index']),
            'Normalized_Restaurant Price Index': float(row['Normalized_Restaurant Price Index']),
            'Normalized_Local Purchasing Power Index': float(row['Normalized_Local Purchasing Power Index'])
        }
    except:
        pass  # Skip if conversion fails

# English display names for some countries that might have non-English names
english_country_names = {
    'Deutschland': 'Germany',
    'España': 'Spain',
    'Россия': 'Russia',
    'Polska': 'Poland',
    'Česko': 'Czech Republic',
    'Österreich': 'Austria',
    'Schweiz': 'Switzerland',
    'Sverige': 'Sweden',
    'Suomi': 'Finland',
    'Norge': 'Norway',
    'Danmark': 'Denmark',
    'Nederland': 'Netherlands',
    'Belgique': 'Belgium',
    'Ελλάδα': 'Greece',
    'България': 'Bulgaria',
    'România': 'Romania',
    'Magyarország': 'Hungary',
    'Slovensko': 'Slovakia',
    'Hrvatska': 'Croatia',
    'Србија': 'Serbia',
    'Ísland': 'Iceland',
    'Slovenija': 'Slovenia',
    'Latvija': 'Latvia',
    'Eesti': 'Estonia',
    'Lietuva': 'Lithuania',
    'Κύπρος': 'Cyprus',
    'Lëtzebuerg': 'Luxembourg',
    'Malta': 'Malta',
    '日本': 'Japan',
    '中国': 'China',
    '대한민국': 'South Korea',
    'भारत': 'India',
    'ประเทศไทย': 'Thailand',
    'Việt Nam': 'Vietnam',
    'Indonesia': 'Indonesia',
    'Россия': 'Russia',
    'Украина': 'Ukraine',
    'Беларусь': 'Belarus',
    'Brasil': 'Brazil',
    'México': 'Mexico',
    'Argentina': 'Argentina',
    'Chile': 'Chile',
    'Perú': 'Peru',
    'Colombia': 'Colombia',
    'Venezuela': 'Venezuela',
    'Türkiye': 'Turkey',
    'مصر': 'Egypt',
    'المغرب': 'Morocco',
    'الجزائر': 'Algeria',
    'تونس': 'Tunisia',
    'ليبيا': 'Libya',
    'السعودية': 'Saudi Arabia',
    'الإمارات': 'UAE',
    'قطر': 'Qatar',
    'الكويت': 'Kuwait',
    'عمان': 'Oman',
    'البحرين': 'Bahrain',
    'لبنان': 'Lebanon',
    'الأردن': 'Jordan',
    'سوريا': 'Syria',
    'العراق': 'Iraq',
    'إيران': 'Iran'
}

# Default to show Cost of Living Index first
default_metric = 'Cost of Living Index'
default_title = 'Cost of Living Index'

# Create a container for the colorbar (now in bottom right)
colorbar_div = folium.Element("""
<div id="dynamic-colorbar" style="position:fixed; right:20px; bottom:20px; z-index:9999; background:white; padding:5px; border-radius:5px; box-shadow: 0 0 10px rgba(0,0,0,0.2);"></div>
""")
world_map.get_root().html.add_child(colorbar_div)

# Define different color schemes for each metric (using distinct colors for each)
color_schemes = {
    'Cost of Living Index': ['#ffcccc', '#ffb3b3', '#ff9999', '#ff8080', '#ff4d4d', '#cc0000'],  # Red scheme
    'Rank': ['#e6ccb3', '#d9b38c', '#cc9966', '#bf8040', '#995c00', '#663d00'],                  # Brown scheme
    'Rent Index': ['#e6ccff', '#d9b3ff', '#cc99ff', '#b366ff', '#9933ff', '#6600cc'],            # Purple scheme
    'Cost of Living Plus Rent Index': ['#cce6ff', '#99ccff', '#66b3ff', '#3399ff', '#0080ff', '#004d99'],  # Blue scheme
    'Groceries Index': ['#ccffcc', '#99ff99', '#66ff66', '#33cc33', '#00b300', '#006600'],       # Green scheme
    'Restaurant Price Index': ['#ffcce6', '#ff99cc', '#ff66b3', '#ff3399', '#cc0066', '#990066'],  # Pink scheme
    'Local Purchasing Power Index': ['#ffe6cc', '#ffcc99', '#ffb366', '#ff9933', '#cc7a00', '#995c00']  # Orange scheme
}

# Define which metrics should use inverted color scales (where higher values are better)
inverted_metrics = ['Local Purchasing Power Index']

# Create colormaps for each metric
colormaps = {}
colorbar_htmls = {}

for col, title in metrics:
    # Use the normalized column
    norm_col = f'Normalized_{col}'
    
    # Set fixed min/max for normalized data (0-100)
    vmin = 0
    vmax = 100
    
    # Create fixed steps for the color scale
    steps = [0, 20, 40, 60, 80, 100]
    
    # Get the color scheme for this metric
    colors = color_schemes[col]
    
    # Choose color order based on metric type
    if col in inverted_metrics or col == 'Rank':
        # For metrics where higher values are better (like purchasing power) or Rank (where lower is better but we've inverted it)
        colormap = cm.LinearColormap(
            colors=colors,
            index=steps,
            vmin=vmin,
            vmax=vmax,
            caption=f"{title}"
        )
    else:
        # For metrics where lower values are better (like cost of living)
        colormap = cm.LinearColormap(
            colors=list(reversed(colors)),  # Reverse colors for the opposite effect
            index=steps,
            vmin=vmin,
            vmax=vmax,
            caption=f"{title}"
        )
    
    colormaps[col] = colormap
    # Store colorbar HTML for this metric
    colorbar_htmls[title] = colormap._repr_html_()

# Create a feature group for each metric
feature_groups = {}
for col, title in metrics:
    # Create a feature group
    fg = folium.FeatureGroup(name=title, show=(title == default_title))
    feature_groups[title] = fg
    
    # Use normalized column for styling
    norm_col = f'Normalized_{col}'
    
    # Define a style function for this metric
    def style_function(feature, col=col, norm_col=norm_col, colormap=colormaps[col]):
        country_name = feature['properties']['name']
        if country_name in country_data and norm_col in country_data[country_name]:
            return {
                'fillColor': colormap(country_data[country_name][norm_col]),
                'color': 'black',
                'weight': 0.5,
                'fillOpacity': 0.7
            }
        else:
            return {'fillColor': '#f0f0f0', 'color': 'black', 'weight': 0.5, 'fillOpacity': 0.3}

    # Create a tooltip function for this layer and metric
    def tooltip_function(feature, col=col, norm_col=norm_col, title=title):
        country_name = feature['properties']['name']
        
        # Use English name if available
        display_name = english_country_names.get(country_name, country_name)
        
        if country_name in country_data:
            data = country_data[country_name]
            
            # Handle metric value formatting
            if col in data:
                orig_value = f"{data[col]:.1f}"
                
                popup_content = f"""
                <div style="min-width:200px">
                    <h4 style="margin:0 0 5px;padding-bottom:5px;border-bottom:1px solid #ccc; font-weight:bold; font-size:16px;">{display_name}</h4>
                    <table style="width:100%;border-collapse:collapse;font-size:13px; margin-top:5px;">
                        <tr><td><b>Rank:</b></td><td align="right">{data['Rank']}</td></tr>
                        <tr><td><b>Cost of Living:</b></td><td align="right">{data['Cost of Living Index']:.1f}</td></tr>
                        <tr><td><b>Rent:</b></td><td align="right">{data['Rent Index']:.1f}</td></tr>
                        <tr><td><b>Groceries:</b></td><td align="right">{data['Groceries Index']:.1f}</td></tr>
                        <tr><td><b>Restaurant:</b></td><td align="right">{data['Restaurant Price Index']:.1f}</td></tr>
                        <tr><td><b>Purchasing Power:</b></td><td align="right">{data['Local Purchasing Power Index']:.1f}</td></tr>
                    </table>
                    <div style="margin-top:8px;font-weight:bold;color:#c00; font-size:14px;">
                        Current View: {title}
                    </div>
                </div>
                """
                return popup_content
            else:
                return f"<b>{display_name}</b><br>No data available"
        else:
            return f"<b>{display_name}</b><br>No data available"

    # Add the GeoJSON layer with tooltips for this metric
    geo_json = folium.GeoJson(
        geo_data,
        name=title,
        style_function=style_function,
        highlight_function=lambda x: {'weight': 2, 'color': '#333333', 'fillOpacity': 0.8}
    )
    
    # Now add tooltips to each country
    folium.features.GeoJsonTooltip(
        fields=['name'],
        aliases=['Country'],
        style=('background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;')
    ).add_to(geo_json)
    
    # Add the GeoJSON layer to the feature group
    geo_json.add_to(fg)
    
    # Now add custom tooltips and country labels with improved geometric placement
    for feature in geo_data['features']:
        country_name = feature['properties']['name']
        display_name = english_country_names.get(country_name, country_name)
        
        if country_name in country_data:
            try:
                # Convert the geometry to a shapely object
                country_geom = shape(feature['geometry'])
                
                # Handle MultiPolygon (countries with multiple parts like islands)
                if country_geom.geom_type == 'MultiPolygon':
                    # Find the largest polygon in the MultiPolygon
                    largest_polygon = max(country_geom.geoms, key=lambda a: a.area)
                    # Use representative_point which guarantees the point is within the polygon
                    label_point = largest_polygon.representative_point()
                else:
                    # For simple polygons, just use representative_point
                    label_point = country_geom.representative_point()
                
                # Get the coordinates from the point
                center = (label_point.y, label_point.x)  # Folium uses (lat, lon)
                
                # Only add labels for countries with area above threshold (to avoid cluttering)
                if country_geom.area > 0.5:  # Threshold can be adjusted
                    # Create a hover tooltip for this country
                    tooltip_html = tooltip_function(feature)
                    
                    # Create a div icon with class for JavaScript to control
                    icon = folium.DivIcon(
                        icon_size=(100, 20),
                        icon_anchor=(50, 10),
                        html=f'''
                            <div class="country-label" 
                                 data-country="{country_name}" 
                                 data-area="{country_geom.area:.2f}" 
                                 style="font-size: 10px; 
                                        color: #333; 
                                        font-weight: bold; 
                                        text-shadow: 1px 1px 1px #fff, -1px -1px 1px #fff, 1px -1px 1px #fff, -1px 1px 1px #fff; 
                                        text-align: center;">
                                {display_name}
                            </div>
                        '''
                    )
                    
                    # Add the label marker
                    marker = folium.Marker(
                        location=center,
                        icon=icon,
                        tooltip=folium.Tooltip(tooltip_html, sticky=True)
                    )
                    marker.add_to(fg)
            except Exception as e:
                # Skip countries where geometry calculations fail
                print(f"Error processing {country_name}: {e}")
                continue
    
    # Add this feature group to the map
    fg.add_to(world_map)

# Add layer control to toggle between metrics
folium.LayerControl(collapsed=False).add_to(world_map)

# Create a dynamic title header for the map
header_html = """
<div id="dynamic-title" style="position:fixed; top:10px; left:50%; transform:translateX(-50%); 
    z-index:9999; background:white; padding:5px 10px; border-radius:5px; 
    font-family:Arial; font-weight:bold; font-size:16px; 
    box-shadow: 0 0 10px rgba(0,0,0,0.2);">
    Global Cost of Living - <span id="metric-title">Cost of Living Index</span>
</div>
"""
world_map.get_root().html.add_child(folium.Element(header_html))

# Add JavaScript to handle layer switching, dynamic colorbar, and dynamic title
js_code = """
<script>
(function() {
    // Store all colorbar HTMLs
    var colorbarHTMLs = {
"""

# Add each metric's colorbar HTML as a JavaScript string
for i, (_, title) in enumerate(metrics):
    if i > 0:
        js_code += ",\n"
    # Properly escape the HTML for JavaScript
    html_escaped = colorbar_htmls[title].replace('\\', '\\\\').replace("'", "\\'").replace('\n', '\\n')
    js_code += f"        '{title}': '{html_escaped}'"

js_code += """
    };
    
    // Function to update the colorbar and title
    function updateColorbarAndTitle(layerName) {
        var colorbarDiv = document.getElementById('dynamic-colorbar');
        var titleSpan = document.getElementById('metric-title');
        
        if (colorbarHTMLs[layerName]) {
            colorbarDiv.innerHTML = colorbarHTMLs[layerName];
        }
        
        if (titleSpan) {
            titleSpan.textContent = layerName;
        }
    }
    
    // Function to handle responsive country labels
    function updateCountryLabels(zoomLevel) {
        var labels = document.querySelectorAll('.country-label');
        
        labels.forEach(function(label) {
            var countryArea = parseFloat(label.getAttribute('data-area') || '0');
            
            // Scale font size based on zoom level and country area
            var baseFontSize = 10;
            var scaleFactor = Math.min(zoomLevel / 2, 2.5);
            
            // Adjust font size based on country size and zoom level
            if (zoomLevel < 3) {
                // At lower zoom levels, only show larger countries
                if (countryArea < 5) {
                    label.style.display = 'none';
                } else {
                    label.style.display = 'block';
                    var fontSize = Math.max(baseFontSize * scaleFactor * 0.8, 8);
                    label.style.fontSize = fontSize + 'px';
                }
            } else if (zoomLevel < 5) {
                // At medium zoom levels, show medium and larger countries
                if (countryArea < 1) {
                    label.style.display = 'none';
                } else {
                    label.style.display = 'block';
                    var fontSize = Math.max(baseFontSize * scaleFactor * 0.9, 9);
                    label.style.fontSize = fontSize + 'px';
                }
            } else {
                // At higher zoom levels, show all countries
                label.style.display = 'block';
                var fontSize = Math.max(baseFontSize * scaleFactor, 10);
                label.style.fontSize = fontSize + 'px';
            }
            
            // Make labels more visible at higher zoom levels
            var opacity = Math.min(1, 0.7 + (zoomLevel - 2) * 0.1);
            label.style.opacity = opacity.toString();
        });
    }
    
    // Set default colorbar and title
    setTimeout(function() {
        // Set the initial colorbar
        updateColorbarAndTitle('""" + default_title + """');
        
        // Get map instance
        var map = document.querySelector('.folium-map')._leaflet_map;
        if (map) {
            // Initial update of label sizes
            updateCountryLabels(map.getZoom());
            
            // Listen for zoom changes
            map.on('zoomend', function() {
                updateCountryLabels(map.getZoom());
            });
        }
        
        // Add event listeners to layer control checkboxes after they're fully loaded
        var checkInterval = setInterval(function() {
            var layerControls = document.querySelectorAll('.leaflet-control-layers-overlays input[type="checkbox"]');
            if (layerControls.length > 0) {
                clearInterval(checkInterval);
                
                layerControls.forEach(function(checkbox) {
                    checkbox.addEventListener('change', function() {
                        if (this.checked) {
                            // Get the layer name from the next element (the label)
                            var layerName = this.nextElementSibling.textContent.trim();
                            updateColorbarAndTitle(layerName);
                            
                            // Uncheck all other checkboxes
                            layerControls.forEach(function(cb) {
                                if (cb !== checkbox && cb.checked) {
                                    cb.checked = false;
                                }
                            });
                        }
                    });
                });
            }
        }, 200);
    }, 1000);
})();
</script>
"""

world_map.get_root().html.add_child(folium.Element(js_code))

# Add CSS to make the map fill the container
css = """
<style>
.folium-map {
    width: 100%;
    height: 100vh;
    position: absolute;
    top: 0;
    left: 0;
}
.country-label {
    white-space: nowrap;
    pointer-events: none;
    text-align: center;
    transition: font-size 0.2s ease;
}
.leaflet-tooltip {
    font-family: Arial, sans-serif;
}
/* Better contrast for country labels */
.country-label {
    text-shadow: 
        -1px -1px 0 #fff,
        1px -1px 0 #fff,
        -1px 1px 0 #fff,
        1px 1px 0 #fff,
        0 -2px 0 #fff,
        0 2px 0 #fff,
        -2px 0 0 #fff,
        2px 0 0 #fff;
    font-weight: bold;
}
</style>
"""
world_map.get_root().html.add_child(folium.Element(css))

# Save the map as an HTML file for Jekyll
world_map.save('global_cost_of_living_map.html')

# Display the map
world_map